In [18]:
import openai
import yaml
import os

import pandas as pd
import numpy as np
import json

# set up GPT

In [19]:
# Use absolute path to the config.yaml file
config_path = "C:/Users/Ryo/OneDrive/Desktop/LLMs/gpt_config.yaml"

In [20]:
with open(config_path) as f:
    config_yaml = yaml.load(f, Loader=yaml.FullLoader)
api_key = config_yaml['token']

client = openai.OpenAI(
    api_key = api_key
)

In [21]:
# select model
# gpt-3.5-turbo-0125 OR gpt-4o-2024-05-13
#model = "gpt-3.5-turbo-0125"
model = "gpt-4o-2024-05-13"

# prepare text data

In [22]:
# Load the Excel file
#file_path = "C:/Users/Ryo/OneDrive/Desktop/Master Thesis/master_thesis/study1/raw/sample_forFeeding.xlsx"
file_path = "C:/Users/Ryo/OneDrive/Desktop/Master Thesis/master_thesis/study1/raw/sample_forFeeding_exactDist.xlsx"

text_set = pd.read_excel(file_path, sheet_name='text_only') 
sample_set = pd.read_excel(file_path, sheet_name='sample')

In [23]:
text_set.head()

posts_filtered
0  I find users with Fi and Ti quite attractive. ...
1  'I'm {MBTI type} and I'd honestly like to know...
2  {html link} back. Good to hear of you. I can't...
3  'oh my god they waste no time hahahahah|||Well...
4  '28 :/|||I like a person that makes me a bette...

In [24]:
sample_set

1st choice 2nd choice 3rd choice  \
0       ENTP       ENFP       INTP   
1       INFP       ISFP       INFJ   
2       ENTP       ENTJ       INTJ   

                   Justification for 1st choice (EI)  \
0  Displays a range of interests and adaptability...   
1  Reflects introspection and a preference for so...   
2  Engages in diverse discussions, suggesting ext...   

                   Justification for 1st choice (NS)  \
0  Shows a preference for exploring abstract idea...   
1  Emphasizes emotional depth and abstract expres...   
2  Prefers theoretical and abstract discussions, ...   

                   Justification for 1st choice (TF)  \
0  Focuses on logical analysis but also values em...   
1  Prioritizes personal values and emotional unde...   
2  Analytical and objective in decision-making, a...   

                   Justification for 1st choice (PJ)  
0  Demonstrates flexibility and spontaneity, char...  
1  Shows a contemplative and open-ended approach ...  
2  Adaptable and open to new ideas, traits of per...

# feed into gpt

In [25]:
keys_list = ['1st choice',	'2nd choice',	'3rd choice',	'Justification for 1st choice (EI)',	'Justification for 1st choice (NS)',	'Justification for 1st choice (TF)',	'Justification for 1st choice (PJ)']

## activate a following cell to conduct a pilot test

In [26]:
tmp_df = text_set.head(10)
tmp_df

posts_filtered
0  I find users with Fi and Ti quite attractive. ...
1  'I'm {MBTI type} and I'd honestly like to know...
2  {html link} back. Good to hear of you. I can't...
3  'oh my god they waste no time hahahahah|||Well...
4  '28 :/|||I like a person that makes me a bette...
5  'A sense of purpose. It's easy to lose that wh...
6  'Momento Mori.|||I often make the mistake of w...
7  'I loved All the Light We Cannot See by Anthon...
8  'I agree with Demtrae. I value my privacy and ...
9  'I can't reasonably validate or contradict the...

## a full commit

In [27]:
# pilot
#target_df = tmp_df
# a full commit
target_df = text_set

In [28]:
results = []

for index, row in target_df.iterrows():
    print(row['posts_filtered'])
    prompt = f"Analyze the given one group of quotes containing multiple posts from the same speaker (each post is splitted using the symbol '|||') and classify him/her according to the Myers-Briggs Personality Indicator (MBTI).  Provide the top three MBTI predictions with justifications only for the first choice focusing on the four core aspects of MBTI: Extraversion vs. Introversion (E vs I), Sensing vs. Intuition (S vs N), Thinking vs. Feeling (T vs F), and Judging vs. Perceiving (J vs P). Make sure your response is in json format ready to be read using json.loads() method properly and follows the template in {sample_set}. Make sure your output contains all keys from {keys_list} and your answers corresponding to each of the keys.  Do not add any additional text in your response. Here's set of quotes {row['posts_filtered']}"
    response = client.chat.completions.create(
        model=model,
        messages=[{"role": "system", "content": "You are a helpful assistant."},
                  {"role": "user", "content": prompt}],
        temperature=1.0,
        max_tokens=500,
        top_p=1.0
    )
    output = response.choices[0].message.content
    print(output)
    try:
        json_data = output.strip('```json\n```')
        try:
            data = json.loads(json_data)
        except json.JSONDecodeError:
            json_data = output.strip('```json\n```  ')
            data = json.loads(json_data)
        results.append(data)
    except json.JSONDecodeError as e:
        print(f"Failed to decode JSON: {e}")
        print("Faulty JSON data:", json_data)  # This will show the problematic part.
        fallback_data = {
            "1st choice": "na",
            "2nd choice": "na",
            "3rd choice": "na",
            "Justification for 1st choice (EI)": "na",
            "Justification for 1st choice (NS)": "na",
            "Justification for 1st choice (TF)": "na",
            "Justification for 1st choice (PJ)": "na"
        }
        results.append(fallback_data)

# Convert results to DataFrame
output_df = pd.DataFrame(results)

output_df.tail(10)

I find users with Fi and Ti quite attractive. I don't understand how someone with Fe can actually be attractive? Fe makes people focus on the other person's needs and stuff and that makes them appear...|||Haha. I really don't think I can stand another like this one. But yeah, I'm thankful too that you could give me such an accurate perspective. I wasn't able to let go because I didn't know if I was...|||I did. I stopped completely. It'll take me a while to heal, haha.    I wouldn't have considered this perspective in a million years. It makes so much sense. I know this was stupid, but I had...|||I have been frank with her from the beginning. What you say makes a lot of sense. I just stopped talking or replying to her messages completely now. Thanks. I guess I came to the right temperament to...|||Thanks.|||Hey, guys,  I met this {MBTI type}(not N) who didn't want a relationship because she said that her past ones had hurt her. We ended up staying friends and I didn't mind that. But one

1st choice 2nd choice 3rd choice  \
614       ISFP       INFP       ESFP   
615       ENFP       ENTP       ENFJ   
616       ENFP       ENTP       INFP   
617       INTP       INTJ       INFP   
618       ENTP       ENTJ       INTJ   
619       ENFP       ENFJ       INFP   
620       ISTJ       INTJ       ISFJ   
621       INFP       ISFP       INFJ   
622       INFP       ENFP       INFJ   
623       ENFP       ENTP       ENFJ   

                     Justification for 1st choice (EI)  \
614  Reflects introspection and a tendency towards ...   
615  Displays a range of interests, enjoys discussi...   
616  Displays a mix of extraversion and introspecti...   
617  The speaker exhibits a clear preference for in...   
618  Engages actively in discussions, showcases a h...   
619  Displays sociability and openness, engaging wi...   
620  The speaker shows a reserved nature, reflectin...   
621  Reflects introspection and a preference for so...   
622  Reflects introspection and a preference for so...   
623  Engages frequently with others, showing enthus...   

                     Justification for 1st choice (NS)  \
614  Engages in discussions that are grounded in pe...   
615  Shows a preference for exploring abstract idea...   
616  Shows a preference for abstract ideas, imagina...   
617  The speaker demonstrates a preference for abst...   
618  Displays a flair for philosophical ideas, abst...   
619  Focuses on abstract concepts, political ideas,...   
620  The speaker focuses on tangible details such a...   
621  Emphasizes emotional depth and abstract expres...   
622  Emphasizes emotional depth and abstract expres...   
623  Shows a preference for exploring ideas, possib...   

                     Justification for 1st choice (TF)  \
614  Shows emotional and empathetic responses, prio...   
615  While capable of logical analysis, there's a n...   
616  Emphasizes personal values, feelings, and emot...   
617  The speaker leans towards thinking by placing ...   
618  Utilizes logical reasoning and objective analy...   
619  Shows a strong orientation towards values and ...   
620  There is a consistent emphasis on logical stru...   
621  Prioritizes personal values and emotional unde...   
622  Prioritizes personal values and emotional unde...   
623  Has a strong preference for understanding and ...   

                     Justification for 1st choice (PJ)  
614  Demonstrates a flexible and spontaneous approa...  
615  Exhibits flexibility and spontaneity in though...  
616  Demonstrates flexibility and spontaneity, freq...  
617  The speaker shows a flexible and adaptable app...  
618  Demonstrates adaptability and spontaneity, eng...  
619  Demonstrates flexibility and a desire to explo...  
620  The speaker values structure, planning, and pu...  
621  Shows a contemplative and open-ended approach ...  
622  Shows a contemplative and open-ended approach ...  
623  Demonstrates flexibility and spontaneity, char...

In [29]:
# Save to Excel
# gpt-4o
#output_df.to_excel("C:/Users/Ryo/OneDrive/Desktop/Master Thesis/master_thesis/study1/raw/gpt4o_result_raw.xlsx", index=False)
# gpt-4o exact distribution
output_df.to_excel("C:/Users/Ryo/OneDrive/Desktop/Master Thesis/master_thesis/study1/raw/gpt4o_result_raw_exactDist.xlsx", index=False)

# gpt-3.5
#output_df.to_excel("C:/Users/Ryo/OneDrive/Desktop/Master Thesis/master_thesis/study1/raw/gpt35_result_raw.xlsx", index=False)
# gpt-3.5 exact distribution
#output_df.to_excel("C:/Users/Ryo/OneDrive/Desktop/Master Thesis/master_thesis/study1/raw/gpt35_result_raw_exactDist.xlsx", index=False)